In [1]:
import numpy as np
import pandas as pd
import json

In [2]:
def format_table(row, maximums):
    '''
    format HTML grade table
    row = numpy array of student scores and comments
    maximums = numpy array listing maximum possible scores
    '''
    
    maximums = ['' if s=='nan' else s for s in maximums.astype(str)]
    row = ['' if s=='nan' else s for s in row.astype(str)]
    
    # format code in instructor's comments
    # *{code}* 
    row = [s.replace('*{', '<code style="color:red;white-space:pre;font-style:normal;display:inline-block;">') for s in row]
    row = [s.replace('}*', '</code>') for s in row]
           
    
    for i in [2,4,6,8,10,12,14]:
        maximums[i] = maximums[i].split('.')[0]
        row[i] = row[i].split('.')[0]
    
    table =[
        r'<table  style="width:100%; table-layout: fixed; border-collapse: collapse; border: 2px solid red; font-size: 110%; color:red; align=left;"><tr style="border: 2px solid red; background-color:Gainsboro"><th style="text-align: left; border: 2px solid red;">Introduction Section: ',
        r'</th><th style="text-align: left; border: 2px solid red;">Conclusions Section: ',
        r'</th><th style="text-align: left; border: 2px solid red;">Content: ',
        r'</th><th style="text-align: left; border: 2px solid red;">Total: ',
        r'</th></tr><tr><td style="border: 2px solid red; text-align: left; font-size: 80%; font-style:italic; vertical-align: text-top;">',
        r'</td><td style="border: 2px solid red; text-align: left; font-size: 80%; font-style:italic; vertical-align: text-top;">',
        r'</td><td style="border: 2px solid red; text-align: left; font-size: 80%; font-style:italic; vertical-align: text-top;">',
        r'</td><td rowspan="3"; style="border: 2px solid red; text-align: left; font-size: 80%; font-style:italic; vertical-align: text-top;">',
        r'</td></tr><tr style="border: 2px solid red; background-color:Gainsboro"><th style="text-align: left; border: 2px solid red;">Code: ',
        r'</th><th style="text-align: left; border: 2px solid red;">Presentation: ',
        r'</th><th style="text-align: left; border: 2px solid red;">Bonus: ',
        r'</th></tr><tr><td style="border: 2px solid red; text-align: left; font-size: 80%; font-style:italic; vertical-align: text-top;">',
        r'</td><td style="border: 2px solid red; text-align: left; font-size: 80%; font-style:italic; vertical-align: text-top;">',
        r'</td><td style="border: 2px solid red; text-align: left; font-size: 80%; font-style:italic; vertical-align: text-top;">',
        r'</td></tr></table>'
       ]
    
    
    score_table = (
                     table[0]                         # table header
                   + row[2] + '/' + maximums[2]       # Intro score
                   + table[1]
                   + row[4] + '/' + maximums[4]       # Conclusions score
                   + table[2]
                   + row[6] + '/' + maximums[6]       # Content score
                   + table[3]
                   + row[14] + '/' + maximums[14]     # Total score
                   + table[4]
                   + row[3]                           # Intro comment
                   + table[5]
                   + row[5]                           # Conclusions comment
                   + table[6]
                   + row[7]                           # Content comment
                   + table[7]
                   + row[15]                          # Total comment
                   + table[8]
                   + row[8] + '/' + maximums[8]       # Code score
                   + table[9]
                   + row[10] + '/' + maximums[10]     # Presentation score
                   + table[10]
                   + row[12]                          # Bonus score
                   + table[11]
                   + row[9]                           # Code comment
                   + table[12]
                   + row[11]                          # Presentation comment
                   + table[13]
                   + row[13]                          # Bonus comment
                   + table[14]
                   )
    
    return score_table

In [32]:
def insert_markdown(nb_dict, new_text):
    '''
    Takes as the argument a dictionary representing Jupyter notebook
    and inserts in it a new first markdown cell containinging new_text
    '''
    
    notebook = nb_dict.copy()
    notebook['cells'].insert(0, {'cell_type': 'markdown', 'metadata': {}, 'source': [new_text]})  
    return notebook

In [4]:
import nbconvert
import nbformat

def notebook_to_html(nb, template='full'):
    """
    Convert a notebook in dictionary object or serialized JSON form to HTML. template
    can be either 'basic' (default) or 'full'. Returns string containing the HTML 
    """
    
    if isinstance(nb, dict):
        json_nb = json.dumps(nb)
    else:
        json_nb = nb

    nnode = nbformat.reads(json_nb, as_version=nbformat.NO_CONVERT)
    exporter = nbconvert.HTMLExporter(config={'Exporter': {'template_file': template}})
    return exporter.from_notebook_node(nnode)[0]

In [14]:
import nbconvert
import nbformat

from  jupyter_contrib_nbextensions.nbconvert_support import EmbedHTMLExporter



def notebook_to_html2(nb, template='full'):
    """
    Convert a notebook in dictionary object or serialized JSON form to HTML. template
    can be either 'basic' (default) or 'full'. Returns string containing the HTML 
    """
    
    if isinstance(nb, dict):
        json_nb = json.dumps(nb)
    else:
        json_nb = nb

    nnode = nbformat.reads(json_nb, as_version=nbformat.NO_CONVERT)
    exporter = EmbedHTMLExporter(config={'Exporter': {'template_file': template}})
    return exporter.from_notebook_node(nnode)[0]

In [33]:
def grading(grade_file, report_num):
    
    nb_path = 'project2_submissions/'
    highligh_css_file = '/Users/bb1/Library/Jupyter/nbextensions/highlighter/highlighter.css'
    
    grades = pd.read_csv(grade_file,   #name of the file
                        delimiter=',',          #the character used to separate columns in the file
                        skiprows= 0,            #this variable can be used to ignore some number of initial rows in the file
                        header = 0,             #the number of row containing column names; if there is no such row set header=None
                        encoding = 'latin1'     #this specifies how text in the file is encoded
                       ).values
    with open(highligh_css_file, 'r') as hcss:
        highlighter = '<style>' + (hcss.read()).replace('\n', ' ') + '<\style>'
       
    
    maximums = grades[0]
    
    for row in grades[1:]: 
        
        if np.isnan(row[0]):
            continue
        
        pnum = str(int(row[0]))

        table = format_table(row, maximums)
        nb_infile = nb_path + 'R' + str(report_num) + '_' + pnum + '.ipynb'
        html_outfile = nb_path + 'R' + str(report_num) + '_' + pnum + '_graded' + '.html'
        
        jfile = open(nb_infile, 'r')
        nb_dict = json.load(jfile)
        jfile.close()
        
        
        # insert grade table
        #notebook = insert_markdown(nb_dict, highlighter)
        
        nb_dict = insert_markdown(nb_dict, 'hello')
        notebook = insert_markdown(nb_dict, table)
        print(notebook)
        
        # convert to html
        html_code = notebook_to_html(notebook)
        
        # save html file
        html_file = open(html_outfile, 'w')
        html_file.write(html_code)
        html_file.close()
        
        print('Finished: ' + 'R' + str(report_num) + '_' + pnum)

In [34]:
grading('grading_template.csv', report_num=2)

{'nbformat_minor': 1, 'cells': [{'source': ['<table  style="width:100%; table-layout: fixed; border-collapse: collapse; border: 2px solid red; font-size: 110%; color:red; align=left;"><tr style="border: 2px solid red; background-color:Gainsboro"><th style="text-align: left; border: 2px solid red;">Introduction Section: /10</th><th style="text-align: left; border: 2px solid red;">Conclusions Section: /10</th><th style="text-align: left; border: 2px solid red;">Content: 18/30</th><th style="text-align: left; border: 2px solid red;">Total: 61/100</th></tr><tr><td style="border: 2px solid red; text-align: left; font-size: 80%; font-style:italic; vertical-align: text-top;"></td><td style="border: 2px solid red; text-align: left; font-size: 80%; font-style:italic; vertical-align: text-top;"></td><td style="border: 2px solid red; text-align: left; font-size: 80%; font-style:italic; vertical-align: text-top;">Unfortunately there are several issues with this report. The goal was to experiment f

Finished: R2_29019719
{'nbformat_minor': 0, 'cells': [{'source': ['<table  style="width:100%; table-layout: fixed; border-collapse: collapse; border: 2px solid red; font-size: 110%; color:red; align=left;"><tr style="border: 2px solid red; background-color:Gainsboro"><th style="text-align: left; border: 2px solid red;">Introduction Section: /10</th><th style="text-align: left; border: 2px solid red;">Conclusions Section: /10</th><th style="text-align: left; border: 2px solid red;">Content: 32/30</th><th style="text-align: left; border: 2px solid red;">Total: 92/100</th></tr><tr><td style="border: 2px solid red; text-align: left; font-size: 80%; font-style:italic; vertical-align: text-top;"></td><td style="border: 2px solid red; text-align: left; font-size: 80%; font-style:italic; vertical-align: text-top;"></td><td style="border: 2px solid red; text-align: left; font-size: 80%; font-style:italic; vertical-align: text-top;">The expected content is here, but the analysis of circle packin

Finished: R2_50079708
{'nbformat_minor': 0, 'cells': [{'source': ['<table  style="width:100%; table-layout: fixed; border-collapse: collapse; border: 2px solid red; font-size: 110%; color:red; align=left;"><tr style="border: 2px solid red; background-color:Gainsboro"><th style="text-align: left; border: 2px solid red;">Introduction Section: /10</th><th style="text-align: left; border: 2px solid red;">Conclusions Section: /10</th><th style="text-align: left; border: 2px solid red;">Content: 30/30</th><th style="text-align: left; border: 2px solid red;">Total: 85/100</th></tr><tr><td style="border: 2px solid red; text-align: left; font-size: 80%; font-style:italic; vertical-align: text-top;"></td><td style="border: 2px solid red; text-align: left; font-size: 80%; font-style:italic; vertical-align: text-top;"></td><td style="border: 2px solid red; text-align: left; font-size: 80%; font-style:italic; vertical-align: text-top;">The is some interesting content here, but the analysis of circl

Finished: R2_50076840
